#### Imports

In [1]:
import json

from nltk import CFG
from nltk.parse.generate import generate

#### Read in files

In [102]:
# change paths if needed
with open('grammar.txt', 'r', encoding='utf-8') as file:
    rules = file.read().split('Production rules for 1st item utterances\n')[1]
model = json.load(open('interaction_model.json', 'r', encoding='utf-8'))

In [46]:
print(rules)

S -> O | O L | P O | P O L | L O | L P O
O -> object | article object | adjective object | article adjective object | particle adjective object | particle article adjective object | particle article o
L -> L L | L image | particle L | location | location_transitive O | location_ditransitive O 'und' O
P -> v



### Create grammar
- extract slots from interaction model
- create grammar from production rules

In [99]:
# create a dictionary from interaction model slots {slot: list of slot values and synonyms}
slots = dict()
for s in model["interactionModel"]["languageModel"]["types"]:
    slots[s['name']] = list()
    for v in s['values']:
        if 'synonyms' in v['name']:
            slots[s['name']] += v['name']['synonyms']
        slots[s['name']] += [v['name']['value']]
    # replace ' by `
    for slot, index in zip(slots[s['name']], range(len(slots[s['name']]))):
        slots[s['name']][index] = slot.replace('\'', '`')

In [ ]:
# TODO recreate grammar from intent
intent = 'ItemsIntent'
model["interactionModel"]["languageModel"]["intents"][intent]

In [103]:
# add terminal rules extracted from slots
for s, v in slots.items():
    values = ' | '.join([f'\'{val}\'' for val in v])
    rule = f'{s} -> {values}\n'
    rules += rule

In [104]:
print(rules)

S -> O | O L | P O | P O L | L O | L P O
O -> object | article object | adjective object | article adjective object | particle adjective object | particle article adjective object | particle article object
L -> L L | L image | particle L | location | location_transitive O | location_ditransitive O 'und' O
P -> verb
article -> 'wat' | 'was' | 'etwas' | 'dat' | 'des' | 'dor' | 'ditt' | 'dit' | 'diesem' | 'diesen' | 'dieses' | 'diese' | 'dieser' | 'so eine' | 'so einen' | 'so ein' | 'eine' | 'einen' | 'einem' | 'ein' | 'dem' | 'den' | 'das' | 'die' | 'der'
object -> 'Absolvent' | 'Student' | 'Gesicht' | 'Smiley' | 'Sterne' | 'Stern' | 'Bildschirm' | 'Podest' | 'Binärcode' | 'Stühle' | 'Stuhl' | 'Seeigel' | 'Mine' | 'Pfeile' | 'Pfeil' | 'Legobaustein' | 'Legostein' | 'Tisch' | 'ABC' | 'Molekül' | 'Atom' | 'Schrank' | 'Delfin' | 'Medaille' | 'Tauben' | 'Taube' | 'Vögel' | 'Vogel' | 'Pfeile' | 'Pfeil' | 'Regenbogen' | 'Reagenzglas' | 'Schultasche' | 'Säulen' | 'Spinne' | 'Wolken' | 'Wolke' |

In [105]:
grammar = CFG.fromstring(rules)
grammar

<Grammar with 331 productions>

In [108]:
grammar.productions()

[S -> O,
 S -> O L,
 S -> P O,
 S -> P O L,
 S -> L O,
 S -> L P O,
 O -> object,
 O -> article object,
 O -> adjective object,
 O -> article adjective object,
 O -> particle adjective object,
 O -> particle article adjective object,
 O -> particle article object,
 L -> L L,
 L -> L image,
 L -> particle L,
 L -> location,
 L -> location_transitive O,
 L -> location_ditransitive O 'und' O,
 P -> verb,
 article -> 'wat',
 article -> 'was',
 article -> 'etwas',
 article -> 'dat',
 article -> 'des',
 article -> 'dor',
 article -> 'ditt',
 article -> 'dit',
 article -> 'diesem',
 article -> 'diesen',
 article -> 'dieses',
 article -> 'diese',
 article -> 'dieser',
 article -> 'so eine',
 article -> 'so einen',
 article -> 'so ein',
 article -> 'eine',
 article -> 'einen',
 article -> 'einem',
 article -> 'ein',
 article -> 'dem',
 article -> 'den',
 article -> 'das',
 article -> 'die',
 article -> 'der',
 object -> 'Absolvent',
 object -> 'Student',
 object -> 'Gesicht',
 object -> 'Smiley

### Generate utterances

In [106]:
def sentences_per_depth(g):
    for i in range(10):
        print('-'*50 + f'\nDEPTH{i}')
        for sentence in generate(g, depth=i):
            print(' '.join(sentence))

In [109]:
def sent_dep(g, d):
    for sentence in generate(g, depth=d):
            print(' '.join(sentence))

In [110]:
sent_dep(grammar, 5)

Absolvent
Student
Gesicht
Smiley
Sterne
Stern
Bildschirm
Podest
Binärcode
Stühle
Stuhl
Seeigel
Mine
Pfeile
Pfeil
Legobaustein
Legostein
Tisch
ABC
Molekül
Atom
Schrank
Delfin
Medaille
Tauben
Taube
Vögel
Vogel
Pfeile
Pfeil
Regenbogen
Reagenzglas
Schultasche
Säulen
Spinne
Wolken
Wolke
Blumentopf
Pflanze
Treppe
Lineal
Büro
Schreibtisch
Giraffenkopf
Giraffe
Zahnrad
other
Sachen
Sache
Teile
Gegenstände
Dinger
Dingens
Dings
Objekt
Gegenstand
Teil
Ding
Uhr
Buchstabenwürfel
Würfel
Programmfenster
Bildschirm
Computerbildschirm
Konsole
Terminal
Fernrohr
Teleskop
Schultafel
Tafel
Schreibutensil
Buntstift
Stift
Gameboy
Switch
Spielekonsole
Spielkonsole
Spaceshuttle
Flugzeug
Raumschiff
Saturn
Planet
Ärztin
Arzt
Ingenieurin
Ingenieur
Mann
Frau
Wissenschaftlerin
Wissenschaftler
Forscherin
Forscher
Personen
Mensch
Person
Teleskop
Mikroskop
Kasten
Lab
Labor
Grafiken
Diagramm
Wellen
Kurven
Birne
Glühbirne
Screen
Gleichung
Demo
Klimaaktivistinnen
Klimaaktivisten
Fridays for Future
FFF
Kinder mit Flagge
Fr

dit Würfel
dit Programmfenster
dit Bildschirm
dit Computerbildschirm
dit Konsole
dit Terminal
dit Fernrohr
dit Teleskop
dit Schultafel
dit Tafel
dit Schreibutensil
dit Buntstift
dit Stift
dit Gameboy
dit Switch
dit Spielekonsole
dit Spielkonsole
dit Spaceshuttle
dit Flugzeug
dit Raumschiff
dit Saturn
dit Planet
dit Ärztin
dit Arzt
dit Ingenieurin
dit Ingenieur
dit Mann
dit Frau
dit Wissenschaftlerin
dit Wissenschaftler
dit Forscherin
dit Forscher
dit Personen
dit Mensch
dit Person
dit Teleskop
dit Mikroskop
dit Kasten
dit Lab
dit Labor
dit Grafiken
dit Diagramm
dit Wellen
dit Kurven
dit Birne
dit Glühbirne
dit Screen
dit Gleichung
dit Demo
dit Klimaaktivistinnen
dit Klimaaktivisten
dit Fridays for Future
dit FFF
dit Kinder mit Flagge
dit Friends For Future
dit Friends
dit Future
dit Kinder
dit Flagge
dit Fahne
dit EU
dit Europaflagge
dit Europa
dit Tafel
dit Koordinatensystem
dit Diagramm
dit Heft
dit Buch
dit Schiff
dit Boot
dit Drillinge
dit Raumfahrerinnen
dit Frauen
dit Astronautin

so einen Uhr
so einen Buchstabenwürfel
so einen Würfel
so einen Programmfenster
so einen Bildschirm
so einen Computerbildschirm
so einen Konsole
so einen Terminal
so einen Fernrohr
so einen Teleskop
so einen Schultafel
so einen Tafel
so einen Schreibutensil
so einen Buntstift
so einen Stift
so einen Gameboy
so einen Switch
so einen Spielekonsole
so einen Spielkonsole
so einen Spaceshuttle
so einen Flugzeug
so einen Raumschiff
so einen Saturn
so einen Planet
so einen Ärztin
so einen Arzt
so einen Ingenieurin
so einen Ingenieur
so einen Mann
so einen Frau
so einen Wissenschaftlerin
so einen Wissenschaftler
so einen Forscherin
so einen Forscher
so einen Personen
so einen Mensch
so einen Person
so einen Teleskop
so einen Mikroskop
so einen Kasten
so einen Lab
so einen Labor
so einen Grafiken
so einen Diagramm
so einen Wellen
so einen Kurven
so einen Birne
so einen Glühbirne
so einen Screen
so einen Gleichung
so einen Demo
so einen Klimaaktivistinnen
so einen Klimaaktivisten
so einen Friday

den Ding
den Uhr
den Buchstabenwürfel
den Würfel
den Programmfenster
den Bildschirm
den Computerbildschirm
den Konsole
den Terminal
den Fernrohr
den Teleskop
den Schultafel
den Tafel
den Schreibutensil
den Buntstift
den Stift
den Gameboy
den Switch
den Spielekonsole
den Spielkonsole
den Spaceshuttle
den Flugzeug
den Raumschiff
den Saturn
den Planet
den Ärztin
den Arzt
den Ingenieurin
den Ingenieur
den Mann
den Frau
den Wissenschaftlerin
den Wissenschaftler
den Forscherin
den Forscher
den Personen
den Mensch
den Person
den Teleskop
den Mikroskop
den Kasten
den Lab
den Labor
den Grafiken
den Diagramm
den Wellen
den Kurven
den Birne
den Glühbirne
den Screen
den Gleichung
den Demo
den Klimaaktivistinnen
den Klimaaktivisten
den Fridays for Future
den FFF
den Kinder mit Flagge
den Friends For Future
den Friends
den Future
den Kinder
den Flagge
den Fahne
den EU
den Europaflagge
den Europa
den Tafel
den Koordinatensystem
den Diagramm
den Heft
den Buch
den Schiff
den Boot
den Drillinge
den Raum

bunten Gegenstand
bunten Teil
bunten Ding
bunten Uhr
bunten Buchstabenwürfel
bunten Würfel
bunten Programmfenster
bunten Bildschirm
bunten Computerbildschirm
bunten Konsole
bunten Terminal
bunten Fernrohr
bunten Teleskop
bunten Schultafel
bunten Tafel
bunten Schreibutensil
bunten Buntstift
bunten Stift
bunten Gameboy
bunten Switch
bunten Spielekonsole
bunten Spielkonsole
bunten Spaceshuttle
bunten Flugzeug
bunten Raumschiff
bunten Saturn
bunten Planet
bunten Ärztin
bunten Arzt
bunten Ingenieurin
bunten Ingenieur
bunten Mann
bunten Frau
bunten Wissenschaftlerin
bunten Wissenschaftler
bunten Forscherin
bunten Forscher
bunten Personen
bunten Mensch
bunten Person
bunten Teleskop
bunten Mikroskop
bunten Kasten
bunten Lab
bunten Labor
bunten Grafiken
bunten Diagramm
bunten Wellen
bunten Kurven
bunten Birne
bunten Glühbirne
bunten Screen
bunten Gleichung
bunten Demo
bunten Klimaaktivistinnen
bunten Klimaaktivisten
bunten Fridays for Future
bunten FFF
bunten Kinder mit Flagge
bunten Friends Fo

...

schräg der gelbe Biene
schräg der gelbe Weltkugel
schräg der gelbe Erdkugel
schräg der gelbe Globus
schräg der gelb Absolvent
schräg der gelb Student
schräg der gelb Gesicht
schräg der gelb Smiley
schräg der gelb Sterne
schräg der gelb Stern
schräg der gelb Bildschirm
schräg der gelb Podest
schräg der gelb Binärcode
schräg der gelb Stühle
schräg der gelb Stuhl
schräg der gelb Seeigel
schräg der gelb Mine
schräg der gelb Pfeile
schräg der gelb Pfeil
schräg der gelb Legobaustein
schräg der gelb Legostein
schräg der gelb Tisch
schräg der gelb ABC
schräg der gelb Molekül
schräg der gelb Atom
schräg der gelb Schrank
schräg der gelb Delfin
schräg der gelb Medaille
schräg der gelb Tauben
schräg der gelb Taube
schräg der gelb Vögel
schräg der gelb Vogel
schräg der gelb Pfeile
schräg der gelb Pfeil
schräg der gelb Regenbogen
schräg der gelb Reagenzglas
schräg der gelb Schultasche
schräg der gelb Säulen
schräg der gelb Spinne
schräg der gelb Wolken
schräg der gelb Wolke
schräg der gelb Blumentop

schräg der kleine Wissenschaftler
schräg der kleine Forscherin
schräg der kleine Forscher
schräg der kleine Personen
schräg der kleine Mensch
schräg der kleine Person
schräg der kleine Teleskop
schräg der kleine Mikroskop
schräg der kleine Kasten
schräg der kleine Lab
schräg der kleine Labor
schräg der kleine Grafiken
schräg der kleine Diagramm
schräg der kleine Wellen
schräg der kleine Kurven
schräg der kleine Birne
schräg der kleine Glühbirne
schräg der kleine Screen
schräg der kleine Gleichung
schräg der kleine Demo
schräg der kleine Klimaaktivistinnen
schräg der kleine Klimaaktivisten
schräg der kleine Fridays for Future
schräg der kleine FFF
schräg der kleine Kinder mit Flagge
schräg der kleine Friends For Future
schräg der kleine Friends
schräg der kleine Future
schräg der kleine Kinder
schräg der kleine Flagge
schräg der kleine Fahne
schräg der kleine EU
schräg der kleine Europaflagge
schräg der kleine Europa
schräg der kleine Tafel
schräg der kleine Koordinatensystem
schräg der

da  wat bunte Terminal
da  wat bunte Fernrohr
da  wat bunte Teleskop
da  wat bunte Schultafel
da  wat bunte Tafel
da  wat bunte Schreibutensil
da  wat bunte Buntstift
da  wat bunte Stift
da  wat bunte Gameboy
da  wat bunte Switch
da  wat bunte Spielekonsole
da  wat bunte Spielkonsole
da  wat bunte Spaceshuttle
da  wat bunte Flugzeug
da  wat bunte Raumschiff
da  wat bunte Saturn
da  wat bunte Planet
da  wat bunte Ärztin
da  wat bunte Arzt
da  wat bunte Ingenieurin
da  wat bunte Ingenieur
da  wat bunte Mann
da  wat bunte Frau
da  wat bunte Wissenschaftlerin
da  wat bunte Wissenschaftler
da  wat bunte Forscherin
da  wat bunte Forscher
da  wat bunte Personen
da  wat bunte Mensch
da  wat bunte Person
da  wat bunte Teleskop
da  wat bunte Mikroskop
da  wat bunte Kasten
da  wat bunte Lab
da  wat bunte Labor
da  wat bunte Grafiken
da  wat bunte Diagramm
da  wat bunte Wellen
da  wat bunte Kurven
da  wat bunte Birne
da  wat bunte Glühbirne
da  wat bunte Screen
da  wat bunte Gleichung
da  wat bunt

da  wat weiße Computerbildschirm
da  wat weiße Konsole
da  wat weiße Terminal
da  wat weiße Fernrohr
da  wat weiße Teleskop
da  wat weiße Schultafel
da  wat weiße Tafel
da  wat weiße Schreibutensil
da  wat weiße Buntstift
da  wat weiße Stift
da  wat weiße Gameboy
da  wat weiße Switch
da  wat weiße Spielekonsole
da  wat weiße Spielkonsole
da  wat weiße Spaceshuttle
da  wat weiße Flugzeug
da  wat weiße Raumschiff
da  wat weiße Saturn
da  wat weiße Planet
da  wat weiße Ärztin
da  wat weiße Arzt
da  wat weiße Ingenieurin
da  wat weiße Ingenieur
da  wat weiße Mann
da  wat weiße Frau
da  wat weiße Wissenschaftlerin
da  wat weiße Wissenschaftler
da  wat weiße Forscherin
da  wat weiße Forscher
da  wat weiße Personen
da  wat weiße Mensch
da  wat weiße Person
da  wat weiße Teleskop
da  wat weiße Mikroskop
da  wat weiße Kasten
da  wat weiße Lab
da  wat weiße Labor
da  wat weiße Grafiken
da  wat weiße Diagramm
da  wat weiße Wellen
da  wat weiße Kurven
da  wat weiße Birne
da  wat weiße Glühbirne
da

KeyboardInterrupt: 

In [125]:
# generate sentences for a certain object, e.g. 'Reagenzglas'
for sentence in generate(grammar, depth=7, n=1000000):
    if len(sentence) >= 4 and 'Reagenzglas' in sentence:
        print(' '.join(sentence))

schräg wat ähnliche Reagenzglas
schräg wat ähnlich Reagenzglas
schräg wat bunte Reagenzglas
schräg wat bunten Reagenzglas
schräg wat bunt Reagenzglas
schräg wat schwarze Reagenzglas
schräg wat schwarzen Reagenzglas
schräg wat schwarz Reagenzglas
schräg wat weißen Reagenzglas
schräg wat weiße Reagenzglas
schräg wat lächelnde Reagenzglas
schräg wat lächelnd Reagenzglas
schräg wat blaue Reagenzglas
schräg wat blau Reagenzglas
schräg wat roten Reagenzglas
schräg wat rotes Reagenzglas
schräg wat rote Reagenzglas
schräg wat rot Reagenzglas
schräg wat zwei Reagenzglas
schräg wat drei Reagenzglas
schräg wat gelbes Reagenzglas
schräg wat gelbe Reagenzglas
schräg wat gelb Reagenzglas
schräg wat grünen Reagenzglas
schräg wat grüne Reagenzglas
schräg wat grün Reagenzglas
schräg wat große Reagenzglas
schräg wat groß Reagenzglas
schräg wat kleine Reagenzglas
schräg wat klein Reagenzglas
schräg was ähnliche Reagenzglas
schräg was ähnlich Reagenzglas
schräg was bunte Reagenzglas
schräg was bunten Reag

schräg diese lächelnde Reagenzglas
schräg diese lächelnd Reagenzglas
schräg diese blaue Reagenzglas
schräg diese blau Reagenzglas
schräg diese roten Reagenzglas
schräg diese rotes Reagenzglas
schräg diese rote Reagenzglas
schräg diese rot Reagenzglas
schräg diese zwei Reagenzglas
schräg diese drei Reagenzglas
schräg diese gelbes Reagenzglas
schräg diese gelbe Reagenzglas
schräg diese gelb Reagenzglas
schräg diese grünen Reagenzglas
schräg diese grüne Reagenzglas
schräg diese grün Reagenzglas
schräg diese große Reagenzglas
schräg diese groß Reagenzglas
schräg diese kleine Reagenzglas
schräg diese klein Reagenzglas
schräg dieser ähnliche Reagenzglas
schräg dieser ähnlich Reagenzglas
schräg dieser bunte Reagenzglas
schräg dieser bunten Reagenzglas
schräg dieser bunt Reagenzglas
schräg dieser schwarze Reagenzglas
schräg dieser schwarzen Reagenzglas
schräg dieser schwarz Reagenzglas
schräg dieser weißen Reagenzglas
schräg dieser weiße Reagenzglas
schräg dieser lächelnde Reagenzglas
schräg d

schräg das weißen Reagenzglas
schräg das weiße Reagenzglas
schräg das lächelnde Reagenzglas
schräg das lächelnd Reagenzglas
schräg das blaue Reagenzglas
schräg das blau Reagenzglas
schräg das roten Reagenzglas
schräg das rotes Reagenzglas
schräg das rote Reagenzglas
schräg das rot Reagenzglas
schräg das zwei Reagenzglas
schräg das drei Reagenzglas
schräg das gelbes Reagenzglas
schräg das gelbe Reagenzglas
schräg das gelb Reagenzglas
schräg das grünen Reagenzglas
schräg das grüne Reagenzglas
schräg das grün Reagenzglas
schräg das große Reagenzglas
schräg das groß Reagenzglas
schräg das kleine Reagenzglas
schräg das klein Reagenzglas
schräg die ähnliche Reagenzglas
schräg die ähnlich Reagenzglas
schräg die bunte Reagenzglas
schräg die bunten Reagenzglas
schräg die bunt Reagenzglas
schräg die schwarze Reagenzglas
schräg die schwarzen Reagenzglas
schräg die schwarz Reagenzglas
schräg die weißen Reagenzglas
schräg die weiße Reagenzglas
schräg die lächelnde Reagenzglas
schräg die lächelnd Re

da  dit lächelnd Reagenzglas
da  dit blaue Reagenzglas
da  dit blau Reagenzglas
da  dit roten Reagenzglas
da  dit rotes Reagenzglas
da  dit rote Reagenzglas
da  dit rot Reagenzglas
da  dit zwei Reagenzglas
da  dit drei Reagenzglas
da  dit gelbes Reagenzglas
da  dit gelbe Reagenzglas
da  dit gelb Reagenzglas
da  dit grünen Reagenzglas
da  dit grüne Reagenzglas
da  dit grün Reagenzglas
da  dit große Reagenzglas
da  dit groß Reagenzglas
da  dit kleine Reagenzglas
da  dit klein Reagenzglas
da  diesem ähnliche Reagenzglas
da  diesem ähnlich Reagenzglas
da  diesem bunte Reagenzglas
da  diesem bunten Reagenzglas
da  diesem bunt Reagenzglas
da  diesem schwarze Reagenzglas
da  diesem schwarzen Reagenzglas
da  diesem schwarz Reagenzglas
da  diesem weißen Reagenzglas
da  diesem weiße Reagenzglas
da  diesem lächelnde Reagenzglas
da  diesem lächelnd Reagenzglas
da  diesem blaue Reagenzglas
da  diesem blau Reagenzglas
da  diesem roten Reagenzglas
da  diesem rotes Reagenzglas
da  diesem rote Reagenzg

da  ein rotes Reagenzglas
da  ein rote Reagenzglas
da  ein rot Reagenzglas
da  ein zwei Reagenzglas
da  ein drei Reagenzglas
da  ein gelbes Reagenzglas
da  ein gelbe Reagenzglas
da  ein gelb Reagenzglas
da  ein grünen Reagenzglas
da  ein grüne Reagenzglas
da  ein grün Reagenzglas
da  ein große Reagenzglas
da  ein groß Reagenzglas
da  ein kleine Reagenzglas
da  ein klein Reagenzglas
da  dem ähnliche Reagenzglas
da  dem ähnlich Reagenzglas
da  dem bunte Reagenzglas
da  dem bunten Reagenzglas
da  dem bunt Reagenzglas
da  dem schwarze Reagenzglas
da  dem schwarzen Reagenzglas
da  dem schwarz Reagenzglas
da  dem weißen Reagenzglas
da  dem weiße Reagenzglas
da  dem lächelnde Reagenzglas
da  dem lächelnd Reagenzglas
da  dem blaue Reagenzglas
da  dem blau Reagenzglas
da  dem roten Reagenzglas
da  dem rotes Reagenzglas
da  dem rote Reagenzglas
da  dem rot Reagenzglas
da  dem zwei Reagenzglas
da  dem drei Reagenzglas
da  dem gelbes Reagenzglas
da  dem gelbe Reagenzglas
da  dem gelb Reagenzglas
d

...

so  dem lächelnd Reagenzglas
so  dem blaue Reagenzglas
so  dem blau Reagenzglas
so  dem roten Reagenzglas
so  dem rotes Reagenzglas
so  dem rote Reagenzglas
so  dem rot Reagenzglas
so  dem zwei Reagenzglas
so  dem drei Reagenzglas
so  dem gelbes Reagenzglas
so  dem gelbe Reagenzglas
so  dem gelb Reagenzglas
so  dem grünen Reagenzglas
so  dem grüne Reagenzglas
so  dem grün Reagenzglas
so  dem große Reagenzglas
so  dem groß Reagenzglas
so  dem kleine Reagenzglas
so  dem klein Reagenzglas
so  den ähnliche Reagenzglas
so  den ähnlich Reagenzglas
so  den bunte Reagenzglas
so  den bunten Reagenzglas
so  den bunt Reagenzglas
so  den schwarze Reagenzglas
so  den schwarzen Reagenzglas
so  den schwarz Reagenzglas
so  den weißen Reagenzglas
so  den weiße Reagenzglas
so  den lächelnde Reagenzglas
so  den lächelnd Reagenzglas
so  den blaue Reagenzglas
so  den blau Reagenzglas
so  den roten Reagenzglas
so  den rotes Reagenzglas
so  den rote Reagenzglas
so  den rot Reagenzglas
so  den zwei Reagenzgla

halbwegs ditt bunt Reagenzglas
halbwegs ditt schwarze Reagenzglas
halbwegs ditt schwarzen Reagenzglas
halbwegs ditt schwarz Reagenzglas
halbwegs ditt weißen Reagenzglas
halbwegs ditt weiße Reagenzglas
halbwegs ditt lächelnde Reagenzglas
halbwegs ditt lächelnd Reagenzglas
halbwegs ditt blaue Reagenzglas
halbwegs ditt blau Reagenzglas
halbwegs ditt roten Reagenzglas
halbwegs ditt rotes Reagenzglas
halbwegs ditt rote Reagenzglas
halbwegs ditt rot Reagenzglas
halbwegs ditt zwei Reagenzglas
halbwegs ditt drei Reagenzglas
halbwegs ditt gelbes Reagenzglas
halbwegs ditt gelbe Reagenzglas
halbwegs ditt gelb Reagenzglas
halbwegs ditt grünen Reagenzglas
halbwegs ditt grüne Reagenzglas
halbwegs ditt grün Reagenzglas
halbwegs ditt große Reagenzglas
halbwegs ditt groß Reagenzglas
halbwegs ditt kleine Reagenzglas
halbwegs ditt klein Reagenzglas
halbwegs dit ähnliche Reagenzglas
halbwegs dit ähnlich Reagenzglas
halbwegs dit bunte Reagenzglas
halbwegs dit bunten Reagenzglas
halbwegs dit bunt Reagenzgla

halbwegs so ein rotes Reagenzglas
halbwegs so ein rote Reagenzglas
halbwegs so ein rot Reagenzglas
halbwegs so ein zwei Reagenzglas
halbwegs so ein drei Reagenzglas
halbwegs so ein gelbes Reagenzglas
halbwegs so ein gelbe Reagenzglas
halbwegs so ein gelb Reagenzglas
halbwegs so ein grünen Reagenzglas
halbwegs so ein grüne Reagenzglas
halbwegs so ein grün Reagenzglas
halbwegs so ein große Reagenzglas
halbwegs so ein groß Reagenzglas
halbwegs so ein kleine Reagenzglas
halbwegs so ein klein Reagenzglas
halbwegs eine ähnliche Reagenzglas
halbwegs eine ähnlich Reagenzglas
halbwegs eine bunte Reagenzglas
halbwegs eine bunten Reagenzglas
halbwegs eine bunt Reagenzglas
halbwegs eine schwarze Reagenzglas
halbwegs eine schwarzen Reagenzglas
halbwegs eine schwarz Reagenzglas
halbwegs eine weißen Reagenzglas
halbwegs eine weiße Reagenzglas
halbwegs eine lächelnde Reagenzglas
halbwegs eine lächelnd Reagenzglas
halbwegs eine blaue Reagenzglas
halbwegs eine blau Reagenzglas
halbwegs eine roten Reagen

halbwegs der grünen Reagenzglas
halbwegs der grüne Reagenzglas
halbwegs der grün Reagenzglas
halbwegs der große Reagenzglas
halbwegs der groß Reagenzglas
halbwegs der kleine Reagenzglas
halbwegs der klein Reagenzglas
einigermaßen wat ähnliche Reagenzglas
einigermaßen wat ähnlich Reagenzglas
einigermaßen wat bunte Reagenzglas
einigermaßen wat bunten Reagenzglas
einigermaßen wat bunt Reagenzglas
einigermaßen wat schwarze Reagenzglas
einigermaßen wat schwarzen Reagenzglas
einigermaßen wat schwarz Reagenzglas
einigermaßen wat weißen Reagenzglas
einigermaßen wat weiße Reagenzglas
einigermaßen wat lächelnde Reagenzglas
einigermaßen wat lächelnd Reagenzglas
einigermaßen wat blaue Reagenzglas
einigermaßen wat blau Reagenzglas
einigermaßen wat roten Reagenzglas
einigermaßen wat rotes Reagenzglas
einigermaßen wat rote Reagenzglas
einigermaßen wat rot Reagenzglas
einigermaßen wat zwei Reagenzglas
einigermaßen wat drei Reagenzglas
einigermaßen wat gelbes Reagenzglas
einigermaßen wat gelbe Reagenzg

einigermaßen dieser rote Reagenzglas
einigermaßen dieser rot Reagenzglas
einigermaßen dieser zwei Reagenzglas
einigermaßen dieser drei Reagenzglas
einigermaßen dieser gelbes Reagenzglas
einigermaßen dieser gelbe Reagenzglas
einigermaßen dieser gelb Reagenzglas
einigermaßen dieser grünen Reagenzglas
einigermaßen dieser grüne Reagenzglas
einigermaßen dieser grün Reagenzglas
einigermaßen dieser große Reagenzglas
einigermaßen dieser groß Reagenzglas
einigermaßen dieser kleine Reagenzglas
einigermaßen dieser klein Reagenzglas
einigermaßen so eine ähnliche Reagenzglas
einigermaßen so eine ähnlich Reagenzglas
einigermaßen so eine bunte Reagenzglas
einigermaßen so eine bunten Reagenzglas
einigermaßen so eine bunt Reagenzglas
einigermaßen so eine schwarze Reagenzglas
einigermaßen so eine schwarzen Reagenzglas
einigermaßen so eine schwarz Reagenzglas
einigermaßen so eine weißen Reagenzglas
einigermaßen so eine weiße Reagenzglas
einigermaßen so eine lächelnde Reagenzglas
einigermaßen so eine läch

In [ ]:
# TODO add morph parser to check for congruency, sntf transduce?
# make more complex production rules? how to join objects and their characteristics?
# (avoid sents like "das lächelnde Reagenzglas")
# OR make less complex production rules, e.g. leave adjectives out, only verb+art+object?